In [1]:
# IMPORTS

import os
import numpy as np
import matplotlib.pyplot as plt
import datetime as dt
import warnings
warnings.filterwarnings("ignore")

#from ipywidgets import widgets, interact, Layout, interactive, fixed
from ipywidgets import *
from IPython.display import display, Javascript
from IPython.core.display import HTML

output_box = widgets.Output()

%matplotlib inline

if os.getcwd().split('/')[-1] == 'PSpy-app':
    pass
else:
    paths = os.getcwd().split('/')[:-1]
    newpath = '/' + os.path.join(*paths)+ '/'
    os.chdir(newpath)


from mypysmps.io.read import read
from mypysmps.util.ps_utils import stack_ps
from mypysmps.graph.psdisplay import PSDisplay
from mypysmps.smpswidgets.widget_aux import wchooseFile, wread

concatenate = widgets.Checkbox(value=False,description='Concatenate',disabled=False,indent=False, 
                               layout = Layout(width='100%'))
filename = widgets.Dropdown(options= wchooseFile(), value = 'data/testdata/LongTerm.csv', 
                            layout = Layout(width='100%'))
filename2 = widgets.SelectMultiple(options= wchooseFile(), value = ['data/testdata/LongTerm.csv'], 
                                   layout = Layout(width='100%'))



# App for accessing SMPS data

In [3]:
def run_all(ev):
    display(Javascript('IPython.notebook.execute_cells_below()'))
    with output_box:
        print("loading your file...")
    
    
button = widgets.Button(description="Apply",layout = Layout(width='15%'))
button.on_click(run_all)

uif = HBox([concatenate, button])
uif2 = VBox([filename, filename2, uif])
display(uif2)
#display(button)

In [4]:
if concatenate.value:
    SMPS = read(filename.value)
    SMPS.createTimeDate()
    dunits = SMPS.datetime['units']
    smps_list = []
    date_list = []
    for afilename in filename2.value:
        asmps = read(afilename)
        asmps.createTimeDate()
        smps_list.append(asmps)
        date_list.append(asmps.datetime['data'][0])
    
    datelist = [dt.datetime.strptime(dl, dunits) for dl in date_list]
    smpslist = [x for _,x in sorted(zip(datelist,smps_list))]
    for smps in smpslist:
        SMPS = stack_ps(SMPS, smps, message = False, fill_time = True)
else:
    SMPS = read(filename.value)
    
psd = PSDisplay(SMPS)

sample = widgets.IntSlider(min=1, max=len(SMPS.sample['data'])-1, continuous_update = False, description = 'sample #',layout = Layout(
            width = '70%'
        ))

sfields = widgets.ToggleButtons(options=SMPS.data['variables'], value = SMPS.data['variables'][0], 
                                description='Variable:', disabled=False, button_style='',
                                layout = Layout(width='100%'))
D50line = widgets.Checkbox(value=False,description='D50',disabled=False,indent=False, layout = Layout(width='20%'))
boundaryline = widgets.Checkbox(value=False,description='Boundaries',disabled=False, indent=False, layout = Layout(width='20%'))
indperiods = widgets.Checkbox(value=False,description='24 hour periods',disabled=False,indent=False, 
                              layout = Layout(width='100%'))
starttime = widgets.Text(value='00:00:00', placeholder='HH:MM:SS', description='Start time:', disabled=False, 
                         layout = Layout(width='100%'))
tfields =  widgets.Dropdown(options= np.append(SMPS.data['variables'],list(SMPS.__dict__.keys())), value = 'total_concentration', 
                            description='Variable:', disabled=False, button_style='', layout = Layout(width = '100%'))

clim = widgets.BoundedFloatText( value=2*10**4, min=1*10**1, max=1*10**8,step=1*10**1, description='clim:',
    style = {'description_width': 'initial'}, disabled=False, continuous_update=True, orientation='horizontal',
    readout=True, readout_format='.2f', layout = Layout(width='25%'))
dlim = widgets.BoundedFloatText( value=1*10**3, min=1*10**1, max=1*10**8,step=1*10**1, description='dlim:', disabled=False, continuous_update=True, orientation='horizontal',
    readout=True, readout_format='.2f', layout = Layout(width='25%'))

ylim =  widgets.BoundedFloatText( value=None, min=0, max=1*10**8,step=0.001, description='ylim:', disabled=False, continuous_update=True, orientation='horizontal',
    readout=True, readout_format='.2f', layout = Layout(width='100%'))

diameter = widgets.Dropdown(options = SMPS.diameter['data'], value = SMPS.diameter['data'][0] , description='Diameter:', 
                            disabled=False, button_style='', layout = Layout(width='100%'))

outplot =  widgets.interactive_output(psd.histogram,{'field':sfields,'sample':sample,'add_D50':D50line,'add_boundaries':boundaryline, 'xlim': dlim,'ylim':clim}) 
outplot2 = widgets.interactive_output(psd.plot, {'field':sfields,'clim':clim,'ylim':dlim, 'indicator':sample,'periods':indperiods, 'starttime':starttime})

date = widgets.interactive_output(psd.dateInfo,{'sample':sample})
#outplot3 = widgets.interactive_output(psd.timeLine, {'field':tfields,'ylim':ylim, 'indicator':sample,'periods':indperiods, 'starttime':starttime})
outplot3 = widgets.interactive_output(psd.timeLine, {'field':tfields,'ylim':ylim,'widget': fixed(True),'diameter':diameter,'indicator':sample,'periods':indperiods, 'starttime':starttime})


#ui1 = widgets.HBox([sfields])
#ui2 = widgets.HBox([D50line, boundaryline, clim, dlim])
#uidate = widgets.HBox([date])
#uiperiods = widgets.HBox([indperiods, starttime])
#ui1a = widgets.HBox([tfields, ylim, diameter])
#ui3 = widgets.VBox([ui1, ui2, outplot, sample, uidate, uiperiods, outplot2,ui1a, outplot3], layout = Layout(height='100%'))

                                      
#display(ui3)

In [5]:
uifhe = widgets.VBox([indperiods, starttime])
outpl1 = HBox([uifhe,outplot2])
outpl2 = VBox([sfields,outpl1])
display(outpl2)

In [6]:
duif = widgets.HBox([date], layout = Layout(width = '30%'))
duif2 = widgets.HBox([date, sample])

display(duif2)


In [7]:
tlout = widgets.VBox([tfields, ylim, diameter])
uift = widgets.HBox([outplot3], layout = Layout(width = '100%'))
outplTL = HBox([tlout, uift])
display(outplTL)

In [8]:
uifh = widgets.HBox([D50line, boundaryline, clim, dlim])
uifhp = widgets.HBox([outplot], layout = Layout(width = '100%'))
uifhout = widgets.VBox([uifh, uifhp])
display(uifhout)